http://www.transtats.bts.gov/DL_SelectFields.asp?Table_ID=236&DB_Short_Name=On-Time

In [1]:
# %load utils/imports.py
%matplotlib inline
import numpy as np
import pandas as pd
from utils import *
#from utils.styles import *

# %load utils/plotting.py
import seaborn as sns
from plotly.offline import init_notebook_mode, iplot
import cufflinks as cf

init_notebook_mode()
cf.go_offline()
import re
from __future__ import division

/Users/calvincheung/anaconda/envs/py27/lib/python2.7/site-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')


In [2]:
df = pd.read_csv('flightdelay_all.csv') # flight delay data

In [3]:
# Subset the data for flight from or to San Francisco only
df = df.loc[df.dest == 'SFO']

df = df.reset_index(drop = True)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 162136 entries, 0 to 162135
Data columns (total 13 columns):
Unnamed: 0          162136 non-null int64
year                162136 non-null int64
month               162136 non-null int64
day_of_month        162136 non-null int64
day_of_week         162136 non-null int64
unique_carrier      162136 non-null object
origin              162136 non-null object
dest                162136 non-null object
crs_dep_time        162136 non-null int64
crs_arr_time        162136 non-null int64
distance            162136 non-null float64
crs_elapsed_time    162136 non-null float64
arr_delay           159492 non-null float64
dtypes: float64(3), int64(7), object(3)
memory usage: 16.1+ MB


In [4]:
# definte a function to convert crs_dep_time and crs_arr_time to 24 hour
def time_convert(t):
    time = int(t/100)
    if t%100 >= 30:
        time += 1
    else:
        time = time
    if time == 24:
        time = 0
    elif time > 24:
        print 'Error! cannot over 24'
    return time

df['cdt'] = df.crs_dep_time.apply(time_convert)
df['cat'] = df.crs_arr_time.apply(time_convert)

df = df.drop('crs_dep_time', axis = 1)
df = df.drop('crs_arr_time', axis = 1)

df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 162136 entries, 0 to 162135
Data columns (total 13 columns):
Unnamed: 0          162136 non-null int64
year                162136 non-null int64
month               162136 non-null int64
day_of_month        162136 non-null int64
day_of_week         162136 non-null int64
unique_carrier      162136 non-null object
origin              162136 non-null object
dest                162136 non-null object
distance            162136 non-null float64
crs_elapsed_time    162136 non-null float64
arr_delay           159492 non-null float64
cdt                 162136 non-null int64
cat                 162136 non-null int64
dtypes: float64(3), int64(7), object(3)
memory usage: 16.1+ MB


In [5]:
with_data = df.arr_delay.notnull()
df = df[with_data].reset_index(drop = True)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 159492 entries, 0 to 159491
Data columns (total 13 columns):
Unnamed: 0          159492 non-null int64
year                159492 non-null int64
month               159492 non-null int64
day_of_month        159492 non-null int64
day_of_week         159492 non-null int64
unique_carrier      159492 non-null object
origin              159492 non-null object
dest                159492 non-null object
distance            159492 non-null float64
crs_elapsed_time    159492 non-null float64
arr_delay           159492 non-null float64
cdt                 159492 non-null int64
cat                 159492 non-null int64
dtypes: float64(3), int64(7), object(3)
memory usage: 15.8+ MB


In [6]:
# convert year, month and day_of_week to datetime
df['flight_date'] = pd.to_datetime(df.year.astype(str) + '-' + df.month.astype(str) + '-' + df.day_of_month.astype(str))
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 159492 entries, 0 to 159491
Data columns (total 14 columns):
Unnamed: 0          159492 non-null int64
year                159492 non-null int64
month               159492 non-null int64
day_of_month        159492 non-null int64
day_of_week         159492 non-null int64
unique_carrier      159492 non-null object
origin              159492 non-null object
dest                159492 non-null object
distance            159492 non-null float64
crs_elapsed_time    159492 non-null float64
arr_delay           159492 non-null float64
cdt                 159492 non-null int64
cat                 159492 non-null int64
flight_date         159492 non-null datetime64[ns]
dtypes: datetime64[ns](1), float64(3), int64(7), object(3)
memory usage: 17.0+ MB


# 1D features

In [7]:
# write a function to merge table
def merge_table(df1, df2, df1_col, df2_col, add_columns, col_name):
    # df1 is the original dataframe, df2 is the new column add to df1
    # df1_col and df2_col are the inner join of the two dataframe
    # *add_columns is a list of columns that add to df1, col_name is the list of new columns names
    df1 = df1.reset_index().copy() # add extra index to return order after table join
    col = df1.columns.tolist()
    col[0] = 'o_index' # rename index
    df1.columns = col
    
    df2[df1_col] = df2[df2_col] # add a column in df2 with the same name as df1
    
    join_df = pd.merge(df1, df2, on = df1_col)
    join_df = join_df.sort_values(by='o_index', ascending=True) # need to sort it before adding columns to df1
    join_df = join_df.set_index('o_index', drop = True)
    for c in range(0, len(add_columns)):
        df1[col_name[c]] = join_df[add_columns[c]]
    df1 = df1.drop('o_index', axis = 1)
    return df1

## Create a delay rating

# <font color = 'red'> Rating = number of flights delay (> 30 min or more) / total number of flights in that category

In [8]:
# create a function to create a 1D feature
def feature1d(df, feature1):
    f1d_df = pd.DataFrame()
    f1d_df['d30'] = 10*(df[df.arr_delay > 30].groupby(feature1).count().max(1)/df.groupby(feature1).count().max(1))
    f1d_df['d60'] = 10*(df[df.arr_delay > 60].groupby(feature1).count().max(1)/df.groupby(feature1).count().max(1))
    f1d_df['d90'] = 10*(df[df.arr_delay > 90].groupby(feature1).count().max(1)/df.groupby(feature1).count().max(1))
    f1d_df['d120'] = 10*(df[df.arr_delay > 120].groupby(feature1).count().max(1)/df.groupby(feature1).count().max(1))
    f1d_df['d_mean'] = df.groupby(feature1).arr_delay.mean()
    f1d_df = f1d_df.fillna(0)
    f1d_df = f1d_df.reset_index()
    f1d_df = f1d_df.round(decimals=2)
    return f1d_df

In [9]:
# Delay based on arrive and departure time
cdt_delay_df = feature1d(df, 'cdt')
cat_delay_df = feature1d(df, 'cat')

df = merge_table(df, cdt_delay_df, 'cdt', 'cdt', ['d30', 'd60', 'd90', 'd120', 'd_mean'], ['cdt_d30', 'cdt_d60', 'cdt_d90', 'cdt_d120', 'cdt_dmean'])
df = merge_table(df, cat_delay_df, 'cat', 'cat', ['d30', 'd60', 'd90', 'd120', 'd_mean'], ['cat_d30', 'cat_d60', 'cat_d90', 'cat_d120', 'cat_dmean'])


In [76]:
cdt_delay_df.set_index('cdt').iplot(title = 'Flight delay by departure time', xTitle = 'Time', yTitle = 'rating')

In [77]:
cat_delay_df.set_index('cat').iplot(title = 'Flight delay by arrive time', xTitle = 'Time', yTitle = 'rating')

In [10]:
# Delay based on flight date
date_delay_df = feature1d(df, 'flight_date')
df = merge_table(df, date_delay_df, 'flight_date', 'flight_date', ['d30', 'd60', 'd90', 'd120', 'd_mean'], ['ddd30', 'ddd60', 'ddd90', 'ddd120', 'dddmean'])

In [63]:
date_delay_df.set_index('flight_date').iplot(title = 'Flight delay by date travel', xTitle = 'Date', yTitle = 'rating')

In [12]:
# Delay based on month
month_delay_df = feature1d(df, 'month')
df = merge_table(df, month_delay_df, 'month', 'month', ['d30', 'd60', 'd90', 'd120', 'd_mean'], ['m_d30', 'm_d60', 'm_d90', 'm_d120', 'm_dmean'])


In [62]:
month_delay_df.set_index('month').iplot(kind = 'bar', title = 'Flight delay by month', xTitle = 'Month', yTitle = 'rating')

In [14]:
# Delay based on day of week
wd_delay_df = feature1d(df, 'day_of_week')
df = merge_table(df, wd_delay_df, 'day_of_week', 'day_of_week', ['d30', 'd60', 'd90', 'd120', 'd_mean'], ['wd_d30', 'wd_d60', 'wd_d90', 'wd_d120', 'wd_dmean'])


In [59]:
wd_delay_df.set_index('day_of_week').iplot(kind = 'bar', title = 'Flight delay by day of week', xTitle = 'Week day', yTitle = 'rating')

In [16]:
# Delay based on unique_carrier
uc_delay_df = feature1d(df, 'unique_carrier')
df = merge_table(df, uc_delay_df, 'unique_carrier', 'unique_carrier', ['d30', 'd60', 'd90', 'd120', 'd_mean'], ['uc_d30', 'uc_d60', 'uc_d90', 'uc_d120', 'uc_dmean'])


In [61]:
uc_delay_df.set_index('unique_carrier').iplot(kind = 'bar', title = 'Flight delay by unique_carrier', xTitle = 'Carrier', yTitle = 'rating')

# 2D features

In [18]:
# create a function to create a 2D feature
def feature2d(df, feature1, feature2, delay):
    f2d_df = 10*(df[df.arr_delay > delay].groupby([feature1,feature2]).count().max(1)/df.groupby([feature1,feature2]).count().max(1)).unstack()
    f2d_df = f2d_df.fillna(0)
    f2d_df = f2d_df.round(decimals=2)
    if type(f2d_df.index.tolist()[0]) != str:
        f2d_df.index = f2d_df.index.astype(str)
    if type(f2d_df.columns.tolist()[0]) != str:
        f2d_df.columns = f2d_df.columns.astype(str)
    return f2d_df

In [19]:
# Delay cause by locations and month

month_origin_d30 = feature2d(df, 'origin','month', 30)
month_origin_d60 = feature2d(df, 'origin','month', 60)
month_origin_d90 = feature2d(df, 'origin','month', 90)

#month_origin_d90.columns
def fmonth_origin_d30(row):
    return month_origin_d30.ix[row['origin'], str(row['month'])]
df['month_origin_d30'] = df.apply(fmonth_origin_d30, axis = 1)

def fmonth_origin_d60(row):
    return month_origin_d60.ix[row['origin'], str(row['month'])]
df['month_origin_d60'] = df.apply(fmonth_origin_d60, axis = 1)

def fmonth_origin_d90(row):
    return month_origin_d90.ix[row['origin'], str(row['month'])]
df['month_origin_d90'] = df.apply(fmonth_origin_d90, axis = 1)


In [20]:
(df[df.arr_delay > 30].groupby(['origin','month']).count().max(1)/df.groupby(['origin','month']).count().max(1)).sort_values(ascending=False).head(10)

origin  month
MMH     12       0.666667
ASE     12       0.666667
TUS     8        0.516129
PIT     1        0.500000
MTJ     12       0.500000
OTH     5        0.500000
TUS     12       0.440000
JAC     12       0.428571
ANC     1        0.400000
BZN     4        0.400000
dtype: float64

# <font color = 'red'> Why !!!????

In [21]:
from IPython.display import Image
from IPython.core.display import HTML 
Image(url= "http://goairportshuttle.com/images/site/slider-aspen-1.jpg")

In [22]:
# Delay cause by weekday and arrive time

weekday_arrtime_d30 = feature2d(df, 'cat','day_of_week', 30)
weekday_arrtime_d60 = feature2d(df, 'cat','day_of_week', 60)
weekday_arrtime_d90 = feature2d(df, 'cat','day_of_week', 90)

def fweekday_arrtime_d30(row):
    return weekday_arrtime_d30.ix[str(row['cat']), str(row['day_of_week'])]
df['weekday_arrtime_d30'] = df.apply(fweekday_arrtime_d30, axis = 1)

def fweekday_arrtime_d60(row):
    return weekday_arrtime_d60.ix[str(row['cat']), str(row['day_of_week'])]
df['weekday_arrtime_d60'] = df.apply(fweekday_arrtime_d60, axis = 1)

def fweekday_arrtime_d90(row):
    return weekday_arrtime_d90.ix[str(row['cat']), str(row['day_of_week'])]
df['weekday_arrtime_d90'] = df.apply(fweekday_arrtime_d90, axis = 1)

In [23]:
print 'Arrive time and day of week', '\n'
(df[df.arr_delay > 60].groupby(['cat','day_of_week']).count().max(1)/df.groupby(['cat','day_of_week']).count().max(1)).sort_values(ascending=False).head(10)

Arrive time and day of week 



cat  day_of_week
10   1              0.132816
23   1              0.129693
20   7              0.122340
21   7              0.121966
22   7              0.121484
18   7              0.119225
22   5              0.115968
13   1              0.115290
17   7              0.114903
12   1              0.114627
dtype: float64

In [24]:
# Delay cause by weekday and departure time

weekday_deptime_d30 = feature2d(df, 'cdt','day_of_week', 30)
weekday_deptime_d60 = feature2d(df, 'cdt','day_of_week', 60)
weekday_deptime_d90 = feature2d(df, 'cdt','day_of_week', 90)

def fweekday_deptime_d30(row):
    return weekday_deptime_d30.ix[str(row['cdt']), str(row['day_of_week'])]
df['weekday_deptime_d30'] = df.apply(fweekday_deptime_d30, axis = 1)

def fweekday_deptime_d60(row):
    return weekday_deptime_d60.ix[str(row['cdt']), str(row['day_of_week'])]
df['weekday_deptime_d60'] = df.apply(fweekday_deptime_d60, axis = 1)

def fweekday_deptime_d90(row):
    return weekday_deptime_d90.ix[str(row['cdt']), str(row['day_of_week'])]
df['weekday_deptime_d90'] = df.apply(fweekday_deptime_d90, axis = 1)

In [25]:
print 'Departure time and day of week', '\n'
(df[df.arr_delay > 60].groupby(['cdt','day_of_week']).count().max(1)/df.groupby(['cdt','day_of_week']).count().max(1)).sort_values(ascending=False).head(10)

Departure time and day of week 



cdt  day_of_week
1    5              0.250000
9    1              0.141328
10   1              0.140661
20   7              0.135057
19   7              0.135027
20   5              0.134138
12   1              0.128903
16   7              0.122995
18   7              0.122744
19   1              0.118564
dtype: float64

In [26]:
# carrier delay at specific month
uc_mon_d30 = feature2d(df, 'month','unique_carrier', 30)
uc_mon_d60 = feature2d(df, 'month','unique_carrier', 60)

def fuc_mon_d30(row):
    return uc_mon_d30.ix[str(row['month']), row['unique_carrier']]
df['uc_mon_d30'] = df.apply(fuc_mon_d30, axis = 1)

def fuc_mon_d60(row):
    return uc_mon_d60.ix[str(row['month']), row['unique_carrier']]
df['uc_mon_d60'] = df.apply(fuc_mon_d60, axis = 1)


## December is still dominated!!

In [27]:
(df[df.arr_delay > 60].groupby(['month','unique_carrier']).count().max(1)/df.groupby(['month','unique_carrier']).count().max(1)).sort_values(ascending=False).head(10)

month  unique_carrier
12     F9                0.237705
       VX                0.183959
       OO                0.174112
       AS                0.173210
       B6                0.168399
       WN                0.154733
       DL                0.144444
2      F9                0.140625
12     UA                0.135670
       AA                0.123894
dtype: float64

In [28]:
# Carrier delay at specific origin
uc_origin_d30 = feature2d(df, 'origin','unique_carrier', 30)
uc_origin_d60 = feature2d(df, 'origin','unique_carrier', 60)

def fuc_origin_d30(row):
    return uc_origin_d30.ix[row['origin'], row['unique_carrier']]
df['uc_origin_d30'] = df.apply(fuc_origin_d30, axis = 1)

def fuc_origin_d60(row):
    return uc_origin_d60.ix[row['origin'], row['unique_carrier']]
df['uc_origin_d60'] = df.apply(fuc_origin_d60, axis = 1)

Sometimes, even the delay percentage is high but it actually not that useful...

In [29]:
print (df[df.arr_delay > 60].groupby(['origin','unique_carrier']).count().max(1)/df.groupby(['origin','unique_carrier']).count().max(1)).sort_values(ascending=False).head(10), '\n'
print 'Airport SAT'
print df[df.origin == 'SAT'].groupby('unique_carrier').count().max(1), '\n'
print 'Airport LAS'
print df[df.origin == 'LAS'].groupby('unique_carrier').count().max(1), '\n'
print 'Airport ASE'
print df[df.origin == 'ASE'].groupby('unique_carrier').count().max(1), '\n'

origin  unique_carrier
SAT     UA                0.333333
LAS     F9                0.205882
ASE     OO                0.176471
MSO     OO                0.155556
SUN     OO                0.144737
OTH     OO                0.139098
TUS     OO                0.133527
STL     UA                0.126984
PSP     OO                0.125848
SLC     UA                0.123711
dtype: float64 

Airport SAT
unique_carrier
OO    388
UA      3
dtype: int64 

Airport LAS
unique_carrier
B6     782
F9      68
OO     371
UA    2728
VX    2483
WN    2174
dtype: int64 

Airport ASE
unique_carrier
OO    187
dtype: int64 



In [30]:
rareport = df.groupby(['origin']).count().max(1).sort_values(ascending=True).head(20).index.tolist()
print df[(df.origin.isin(rareport))&(df.arr_delay > 30)].groupby('origin').count().max(1)/df[(df.origin.isin(rareport))].groupby('origin').count().max(1)



origin
ANC    0.123529
ASE    0.251337
BWI    0.053292
BZN    0.194444
CEC    0.184971
COS         NaN
CVG    0.055556
HDN         NaN
JAC    0.158537
MMH    0.229008
MSN         NaN
MSO    0.200000
MSY    0.147541
MTJ    0.206897
OMA         NaN
OTH    0.229323
PIT    0.051020
SUN    0.203947
TPA         NaN
XNA    0.122807
dtype: float64


In [31]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 159492 entries, 0 to 159491
Data columns (total 57 columns):
Unnamed: 0             159492 non-null int64
year                   159492 non-null int64
month                  159492 non-null int64
day_of_month           159492 non-null int64
day_of_week            159492 non-null int64
unique_carrier         159492 non-null object
origin                 159492 non-null object
dest                   159492 non-null object
distance               159492 non-null float64
crs_elapsed_time       159492 non-null float64
arr_delay              159492 non-null float64
cdt                    159492 non-null int64
cat                    159492 non-null int64
flight_date            159492 non-null datetime64[ns]
cdt_d30                159492 non-null float64
cdt_d60                159492 non-null float64
cdt_d90                159492 non-null float64
cdt_d120               159492 non-null float64
cdt_dmean              159492 non-null float64
cat_d3

def timezone(t):
    if (t >= 1) and (t < 10):
        zone = 0
    elif (t >= 10) and (t < 17):
        zone = 1
    else:
        zone = 2
    return zone

df['cat_timezone'] = df.cat.apply(timezone)
df['cdt_timezone'] = df.cdt.apply(timezone)

busy_origin = pd.DataFrame(df.groupby('origin').arr_delay.mean())
busy_origin['volume'] = df.groupby('origin').count().max(1)
busy_origin['delay_volume'] = busy_origin.arr_delay * busy_origin.volume
delay_origin = busy_origin.delay_volume.sort_values(ascending=False).head(10).index.tolist()


def busy_airport(origin):
    if origin in delay_origin:
        busy = 1
    else:
        busy = 0
    return busy

df['busy_airport'] = df.origin.apply(busy_airport)

df.groupby('busy_airport').arr_delay.mean().iplot(kind = 'bar')

In [32]:
# holiday rating
holiday =  pd.read_csv('us_holiday.csv') # holiday data

# add hol_rating
holiday = holiday.drop(holiday.index[365:])
holiday['date'] = pd.to_datetime(holiday['date'])
holiday = holiday.fillna(0)
holiday['hol_rating'] = holiday.weekend + holiday.fed_hol + holiday.a_hol + holiday.l_hol

In [72]:
holiday.head(10)

date d_of_w  weekend  fed_hol  a_hol  l_hol  hol_rating flight_date
0 2015-01-01    Thu      0.0      1.0    1.0    1.0         3.0  2015-01-01
1 2015-02-01    Fri      0.0      0.0    0.0    1.0         1.0  2015-02-01
2 2015-03-01    Sat      1.0      0.0    1.0    1.0         3.0  2015-03-01
3 2015-04-01    Sun      1.0      0.0    1.0    1.0         3.0  2015-04-01
4 2015-05-01    Mon      0.0      0.0    0.0    0.0         0.0  2015-05-01
5 2015-06-01    Tue      0.0      0.0    0.0    0.0         0.0  2015-06-01
6 2015-07-01    Wed      0.0      0.0    0.0    0.0         0.0  2015-07-01
7 2015-08-01    Thu      0.0      0.0    0.0    0.0         0.0  2015-08-01
8 2015-09-01    Fri      0.0      0.0    0.0    0.0         0.0  2015-09-01
9 2015-10-01    Sat      1.0      0.0    1.0    0.0         2.0  2015-10-01

In [33]:
# airport busy level
ap = pd.read_csv('airport_passenger.csv') # airport passenger
# create a rating of airports based on the number of passenger (in 2014), here, we divide the passeger by 1000000
def br(s):
    # s is the string in the columns 'y2014' and 'y2015'
    rating = float(re.sub(r'[^\w]', '', s))/1000000
    return rating
ap['busy_rating'] = ap.y2014.apply(br)

# add variables based on airport busy level
df = merge_table(df, ap, 'origin', 'iata', ['busy_rating'], ['origin_br'])
df = merge_table(df, ap, 'dest', 'iata', ['busy_rating'], ['dest_br'])

# origin_br is a rating of the airport, this rating would be NaN if they are not the top 60 busiest airport
# therefore it is okay to replace these data to 0 

df['origin_br'] = df.origin_br.fillna(0)

In [34]:
# other airport data

airport = pd.read_csv('airports.csv', names = ['name', 'city', 'country', 'iata', 'icao', 'lat', 'lon', 'alt', 'timezone', 'dst', 'tz']) # airport data

# add variables based on airport 
df = merge_table(df, airport, 'origin', 'iata', ['lat', 'lon'], ['origin_lat', 'origin_lon'])
df = merge_table(df, airport, 'dest', 'iata', ['lat', 'lon'], ['dest_lat', 'dest_lon'])
df['trave_lat'] = df.dest_lat - df.origin_lat
df['trave_lon'] = df.dest_lon - df.origin_lon

# add variables based on holidays
if 'weekend' in df.columns: # avoid error during re-run this cell
    df = df.drop(['weekend','fed_hol','a_hol','l_hol','hol_rating'], axis = 1).copy()
df = merge_table(df, holiday, 'flight_date', 'date', ['weekend','fed_hol','a_hol','l_hol','hol_rating'],['weekend','fed_hol','a_hol','l_hol','hol_rating'])

In [78]:
airport.head(10)

name          city           country iata  icao  \
1                       Goroka        Goroka  Papua New Guinea  GKA  AYGA   
2                       Madang        Madang  Papua New Guinea  MAG  AYMD   
3                  Mount Hagen   Mount Hagen  Papua New Guinea  HGU  AYMH   
4                       Nadzab        Nadzab  Papua New Guinea  LAE  AYNZ   
5   Port Moresby Jacksons Intl  Port Moresby  Papua New Guinea  POM  AYPY   
6                   Wewak Intl         Wewak  Papua New Guinea  WWK  AYWK   
7                   Narsarsuaq  Narssarssuaq         Greenland  UAK  BGBW   
8                         Nuuk      Godthaab         Greenland  GOH  BGGH   
9            Sondre Stromfjord   Sondrestrom         Greenland  SFJ  BGSF   
10              Thule Air Base         Thule         Greenland  THU  BGTL   

          lat         lon   alt  timezone dst                    tz origin  \
1   -6.081689  145.391881  5282      10.0   U  Pacific/Port_Moresby    GKA   
2   -5.207083  145.788700    20      10.0   U  Pacific/Port_Moresby    MAG   
3   -5.826789  144.295861  5388      10.0   U  Pacific/Port_Moresby    HGU   
4   -6.569828  146.726242   239      10.0   U  Pacific/Port_Moresby    LAE   
5   -9.443383  147.220050   146      10.0   U  Pacific/Port_Moresby    POM   
6   -3.583828  143.669186    19      10.0   U  Pacific/Port_Moresby    WWK   
7   61.160517  -45.425978   112      -3.0   E       America/Godthab    UAK   
8   64.190922  -51.678064   283      -3.0   E       America/Godthab    GOH   
9   67.016969  -50.689325   165      -3.0   E       America/Godthab    SFJ   
10  76.531203  -68.703161   251      -4.0   E         America/Thule    THU   

   dest  
1   GKA  
2   MAG  
3   HGU  
4   LAE  
5   POM  
6   WWK  
7   UAK  
8   GOH  
9   SFJ  
10  THU

<font color = 'red'> I did try create dummies variables from the categorical data, but they are not that significant in our prediction model...

# Split out design matrix and response vector

In [35]:
# definte a function to convert arrive delay to hour
def delay_time(t):
    time = int(t/60)
    return time

df['delay_time'] = df.arr_delay.apply(delay_time)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 159492 entries, 0 to 159491
Data columns (total 71 columns):
Unnamed: 0             159492 non-null int64
year                   159492 non-null int64
month                  159492 non-null int64
day_of_month           159492 non-null int64
day_of_week            159492 non-null int64
unique_carrier         159492 non-null object
origin                 159492 non-null object
dest                   159492 non-null object
distance               159492 non-null float64
crs_elapsed_time       159492 non-null float64
arr_delay              159492 non-null float64
cdt                    159492 non-null int64
cat                    159492 non-null int64
flight_date            159492 non-null datetime64[ns]
cdt_d30                159492 non-null float64
cdt_d60                159492 non-null float64
cdt_d90                159492 non-null float64
cdt_d120               159492 non-null float64
cdt_dmean              159492 non-null float64
cat_d3

In [36]:
# Check for missing values
is_null = lambda col: sum(pd.isnull(df[col]))
missing_values = [(col,is_null(col)) for col in df if is_null(col)]
missing_values

[]

In [37]:
print df.columns.tolist()

['Unnamed: 0', 'year', 'month', 'day_of_month', 'day_of_week', 'unique_carrier', 'origin', 'dest', 'distance', 'crs_elapsed_time', 'arr_delay', 'cdt', 'cat', 'flight_date', 'cdt_d30', 'cdt_d60', 'cdt_d90', 'cdt_d120', 'cdt_dmean', 'cat_d30', 'cat_d60', 'cat_d90', 'cat_d120', 'cat_dmean', 'ddd30', 'ddd60', 'ddd90', 'ddd120', 'dddmean', 'm_d30', 'm_d60', 'm_d90', 'm_d120', 'm_dmean', 'wd_d30', 'wd_d60', 'wd_d90', 'wd_d120', 'wd_dmean', 'uc_d30', 'uc_d60', 'uc_d90', 'uc_d120', 'uc_dmean', 'month_origin_d30', 'month_origin_d60', 'month_origin_d90', 'weekday_arrtime_d30', 'weekday_arrtime_d60', 'weekday_arrtime_d90', 'weekday_deptime_d30', 'weekday_deptime_d60', 'weekday_deptime_d90', 'uc_mon_d30', 'uc_mon_d60', 'uc_origin_d30', 'uc_origin_d60', 'origin_br', 'dest_br', 'origin_lat', 'origin_lon', 'dest_lat', 'dest_lon', 'trave_lat', 'trave_lon', 'weekend', 'fed_hol', 'a_hol', 'l_hol', 'hol_rating', 'delay_time']


In [38]:
# Our target variable is arrive delay
y = df.delay_time

# Select variables for X

drop_vars = ['Unnamed: 0', 'year', 'month', 'day_of_month', 'day_of_week', 'unique_carrier', 'origin', 'dest', \
             'crs_elapsed_time', 'arr_delay', 'cdt', 'cat', 'flight_date', 'delay_time' ]
X = df.drop(drop_vars,axis=1)
X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 159492 entries, 0 to 159491
Data columns (total 57 columns):
distance               159492 non-null float64
cdt_d30                159492 non-null float64
cdt_d60                159492 non-null float64
cdt_d90                159492 non-null float64
cdt_d120               159492 non-null float64
cdt_dmean              159492 non-null float64
cat_d30                159492 non-null float64
cat_d60                159492 non-null float64
cat_d90                159492 non-null float64
cat_d120               159492 non-null float64
cat_dmean              159492 non-null float64
ddd30                  159492 non-null float64
ddd60                  159492 non-null float64
ddd90                  159492 non-null float64
ddd120                 159492 non-null float64
dddmean                159492 non-null float64
m_d30                  159492 non-null float64
m_d60                  159492 non-null float64
m_d90                  159492 non-null floa

# Feature Selection - check if there any potential relationships between the predictors and the response variable.

In [39]:
from sklearn import feature_selection as fs

def f_regression_feature_selection(input, response):    
# use this against your feature matrix to determine p-values for
# each feature (we care about the second array it returns).
    return fs.univariate_selection.f_regression(input, response)

# F Values statistics test - tests the overall significance of the regression model
(The F value is the ratio of the mean regression sum of squares divided by the mean error sum of squares. Its value will range from zero to an arbitrarily large number, i.e. The null hypothesis is rejected if the F ratio is large, here, let's reject the features if they are smaller than 10.)

In [40]:
# features that they don't meet the F test threshold and who are they:
print sum(f_regression_feature_selection(X,y)[0] < 10)
select = f_regression_feature_selection(X,y)[0] < 10
print X.columns[select]

10
Index([u'dest_br', u'origin_lat', u'dest_lat', u'dest_lon', u'trave_lat',
       u'weekend', u'fed_hol', u'a_hol', u'l_hol', u'hol_rating'],
      dtype='object')


In [41]:
# drop the selected columns
Xs = X[X.columns.difference(X.columns[select])]
Xs.head()

cat_d120  cat_d30  cat_d60  cat_d90  cat_dmean  cdt_d120  cdt_d30  cdt_d60  \
0      0.24     1.64     0.81     0.43       5.43       0.2     1.24     0.64   
1      0.24     1.64     0.81     0.43       5.43       0.2     1.24     0.64   
2      0.24     1.64     0.81     0.43       5.43       0.2     1.24     0.64   
3      0.24     1.64     0.81     0.43       5.43       0.2     1.24     0.64   
4      0.24     1.64     0.81     0.43       5.43       0.2     1.24     0.64   

   cdt_d90  cdt_dmean         ...           wd_d30  wd_d60  wd_d90  wd_dmean  \
0     0.35       2.89         ...             1.53    0.80    0.44      7.04   
1     0.35       2.89         ...             1.53    0.84    0.49      7.32   
2     0.35       2.89         ...             0.91    0.45    0.26     -1.05   
3     0.35       2.89         ...             1.67    0.92    0.56      8.69   
4     0.35       2.89         ...             1.76    0.96    0.54     10.29   

   weekday_arrtime_d30  weekday_arrtime_d60  weekday_arrtime_d90  \
0                 1.71                 0.85                 0.48   
1                 1.53                 0.80                 0.44   
2                 1.00                 0.46                 0.28   
3                 1.51                 0.74                 0.43   
4                 2.19                 1.15                 0.63   

   weekday_deptime_d30  weekday_deptime_d60  weekday_deptime_d90  
0                 1.39                 0.75                 0.38  
1                 1.16                 0.62                 0.35  
2                 0.77                 0.34                 0.22  
3                 1.13                 0.47                 0.23  
4                 1.79                 0.92                 0.48  

[5 rows x 47 columns]

In [42]:
# test features that they don't meet the F test threshold, P < 0.05
sum(f_regression_feature_selection(Xs,y)[1] < 0.05)

47

In [43]:
# Sort the features based on their statistical significance 
ps = f_regression_feature_selection(Xs,y)[1]
p_score = zip(Xs.columns, ps)
ranked_p = sorted(p_score, key=lambda x:x[1])
ranked_p

[('ddd120', 0.0),
 ('ddd30', 0.0),
 ('ddd60', 0.0),
 ('ddd90', 0.0),
 ('dddmean', 0.0),
 ('m_d120', 0.0),
 ('m_d30', 0.0),
 ('m_d60', 0.0),
 ('m_d90', 0.0),
 ('m_dmean', 0.0),
 ('month_origin_d30', 0.0),
 ('month_origin_d60', 0.0),
 ('month_origin_d90', 0.0),
 ('uc_mon_d30', 0.0),
 ('uc_mon_d60', 0.0),
 ('weekday_deptime_d90', 1.9976399229948424e-241),
 ('weekday_deptime_d60', 9.3269077598527024e-235),
 ('weekday_arrtime_d90', 5.9361326862746005e-225),
 ('weekday_arrtime_d60', 4.6066980155103354e-220),
 ('weekday_deptime_d30', 6.4686783866451718e-210),
 ('weekday_arrtime_d30', 5.1498240997998573e-190),
 ('uc_origin_d60', 3.1742677798994934e-148),
 ('uc_origin_d30', 1.8855091687840862e-111),
 ('cdt_d90', 1.0397499156788941e-107),
 ('cdt_dmean', 4.4939573393175973e-104),
 ('cdt_d120', 6.0021177551142606e-104),
 ('cdt_d60', 7.8766652840647579e-104),
 ('cdt_d30', 4.4190589364152532e-98),
 ('wd_d90', 8.0874974108734268e-88),
 ('cat_d90', 2.4717721055301549e-87),
 ('wd_d60', 1.25350980683582

In [44]:
from sklearn.linear_model import Ridge

In [45]:
# Build univariate models to show individual features performs
scores = []
for feat, score in ranked_p:
    est = Ridge()
    X = [[x] for x in Xs[feat]]
    est.fit(X,y)
    scores.append(est.score(X,y))

In [67]:
# Drop of R^2 with strong to weakest features
cols = [k[0] for k in ranked_p]
pd.DataFrame(scores,index=cols).iplot(kind='bar', title = 'Feature performance', yTitle = 'Correlation')

In [47]:
# Build models with combinations of features
scores = []
feats = []
for feat, score in ranked_p:
    est = Ridge()
    feats.append(feat)
    if len(feats) == 1:
        X = [[x] for x in Xs[feat]]
    else:
        X = Xs[feats]
    est.fit(X, y)
    scores.append(est.score(X,y))

In [79]:
pd.DataFrame(scores,index=cols).iplot(kind='bar', title = 'Combinations of features', yTitle = 'Score')

In [49]:
# Now let's build models which cummatively look well combinations of features performs
from sklearn.cross_validation import cross_val_score

scores_cv = []
feats = []
for feat, score in ranked_p:
    est = Ridge()
    feats.append(feat)
    if len(feats) == 1:
        X = [[x] for x in Xs[feat]]
    else:
        X = Xs[feats]
    est.fit(X, y)
    scores_cv.append(cross_val_score(est,X,y).mean())

In [69]:
# Residual plot

res = y-est.predict(X)

pd.DataFrame(res).iplot(kind = 'scatter', mode='markers', size = 5, title = 'Residual plot', yTitle = 'Error (hour)')



In [51]:
# Drop of R^2 with strong to weakest features
# Drop of R^2 with strong to weakest features
# cols = [k[0] for k in ranked_p]
df_cv = pd.DataFrame(scores,index=feats, columns=['regular'])
df_cv['cv'] = scores_cv

df_cv.iplot()

In [52]:
correlation = Xs[[x[0] for x in ranked_p]].corr()
correlation.apply(abs).iplot(kind='heatmap', colorscale='spectral')

In [53]:
p_features = [x[0] for x in ranked_p][:5]
p_features

['ddd120', 'ddd30', 'ddd60', 'ddd90', 'dddmean']

In [54]:
import statsmodels.api as sm

In [55]:
model = sm.OLS(y, X)
results = model.fit()
print results.summary()

                            OLS Regression Results                            
Dep. Variable:             delay_time   R-squared:                       0.097
Model:                            OLS   Adj. R-squared:                  0.096
Method:                 Least Squares   F-statistic:                     370.7
Date:                Tue, 27 Sep 2016   Prob (F-statistic):               0.00
Time:                        18:48:58   Log-Likelihood:            -1.2003e+05
No. Observations:              159492   AIC:                         2.402e+05
Df Residuals:                  159445   BIC:                         2.406e+05
Df Model:                          46                                         
Covariance Type:            nonrobust                                         
                          coef    std err          t      P>|t|      [95.0% Conf. Int.]
---------------------------------------------------------------------------------------
ddd120                  0.1968    